In [133]:
import pandas as pd
import altair as alt
from sklearn.cluster import DBSCAN

In [134]:
alt.themes.enable('fivethirtyeight')

ThemeRegistry.enable('fivethirtyeight')

In [135]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [136]:
# this goes at the top of the notebook
def to_altair(x):    
    x.to_json('chart.json', orient='records', date_format='iso')
    return('chart.json')
pd.DataFrame.to_altair = to_altair # attach to DataFrame objects

In [137]:
# load the PLD for Q1
q1_df = pd.read_csv('data/202302 BIE Technical Interview PLD1.csv')

In [138]:
# initial look at data
q1_df.head()

OrderCount  OriginZip  DestinationZip  Length  Width  Height  WeightOunces
0           1      12409           60197    12.0    9.0     1.0           6.0
1           2      49782           13144     9.0    8.0     6.0          24.0
2           1      42323           80920    12.0    9.0     1.0           6.0
3           1      17072            9499    12.0    9.0     5.0          67.0
4           1      49782           72068     9.0    6.0     4.0          11.0

In [139]:
# see shape of data
q1_df.shape

(1580937, 7)

In [140]:
# view datatypes
q1_df.dtypes

OrderCount          int64
OriginZip           int64
DestinationZip      int64
Length            float64
Width             float64
Height            float64
WeightOunces      float64
dtype: object

In [141]:
# convert zip codes to string so matplotlib recognizes it as categorical instead of numerical
q1_df['OriginZip'] = q1_df['OriginZip'].astype(str)
q1_df['DestinationZip'] = q1_df['DestinationZip'].astype(str)

In [142]:
# looks like leading 0s were dropped from zip codes at some point in exporting or loading the csv, let's fill in these leading 0s. Some are missing 2 leadings 0s and others only one.

print(len(q1_df[q1_df['DestinationZip'].str.len() == 3]), len(q1_df[q1_df['DestinationZip'].str.len() == 4]))

87 127817


In [143]:
# create function to apply to leading 0s to columns
def fill_leading_zeros(x):
    x = x.zfill(5)
    return x

In [144]:
q1_df['OriginZip'] = q1_df['OriginZip'].apply(fill_leading_zeros)
q1_df['DestinationZip'] = q1_df['DestinationZip'].apply(fill_leading_zeros)

In [145]:
q1_df

OrderCount OriginZip DestinationZip  Length  Width  Height   
0                 1     12409          60197    12.0    9.0     1.0  \
1                 2     49782          13144     9.0    8.0     6.0   
2                 1     42323          80920    12.0    9.0     1.0   
3                 1     17072          09499    12.0    9.0     5.0   
4                 1     49782          72068     9.0    6.0     4.0   
...             ...       ...            ...     ...    ...     ...   
1580932           1     12409          40964    11.0    4.0     4.0   
1580933           2     27152          14174    12.0    9.0     5.0   
1580934           1     90061          07963     8.0    7.0     5.0   
1580935           1     36039          93274    14.0   12.0     3.0   
1580936           1     42323          49120    22.0   12.0     5.0   

         WeightOunces  
0                 6.0  
1                24.0  
2                 6.0  
3                67.0  
4                11.0  
...               ...  
1580932          10.0  
1580933          55.0  
1580934          13.0  
1580935          42.0  
1580936          69.0  

[1580937 rows x 7 columns]

In [146]:
# view the distribution of origin zip codes
origin_zips = q1_df['OriginZip'].value_counts(ascending=False).reset_index()

In [147]:
origin_zips

OriginZip   count
0      17072  214441
1      28159  180970
2      36039  179331
3      42323  113596
4      12409   78708
5      90061   71642
6      49782   69506
7      02072   65397
8      27045   58380
9      27152   57055
10     89137   53819
11     12565   38612
12     30521   37433
13     67361   35856
14     56239   28490
15     61341   27105
16     10163   23258
17     52035   22845
18     32958   21822
19     04041   20245
20     33090   19666
21     35972   18890
22     83708   18848
23     28208   18565
24     34211   15961
25     25315   14027
26     98253   12077
27     87056   10191
28     58043    7701
29     47532    6888
30     68840    6372
31     69027    4729
32     16914    4424
33     72070    3538
34     21849    3235
35     70010    3080
36     05775    2831
37     94043    2651
38     11797    2622
39     17013    2071
40     68658    1969
41     16352    1253
42     93280     491
43     59713     340
44     61254       3
45     24161       2
46     59602       1

In [148]:
alt.Chart(origin_zips).mark_bar().encode(
    x=alt.X('OriginZip:N', axis=alt.Axis(title='Origin Zip Code'), sort=None),
    y=alt.Y('count:Q', axis=alt.Axis(title='Count')),
    tooltip=['OriginZip', 'count']
).configure_axisX(
    labels=False
).properties(
    width=2500,
    height=500,
    title='Distribution of Origin Zip Codes'
).configure_title(
    anchor='middle'
)

alt.Chart(...)

In [149]:
# view the distribution of destination zip codes. Convert Zip code to string so matplotlib recognizes it as categorical
destination_zips = q1_df['DestinationZip'].value_counts(ascending=False).reset_index()

In [150]:
destination_zips

DestinationZip  count
0              27529   1089
1              70645    819
2              21015    776
3              32702    775
4              80128    746
...              ...    ...
22375          29653      1
22376          48886      1
22377          77963      1
22378          30277      1
22379          94601      1

[22380 rows x 2 columns]

In [151]:
alt.Chart(destination_zips).mark_bar().encode(
    x=alt.X('DestinationZip:N', axis=alt.Axis(title='Destination Zip Code'), sort=None),
    y=alt.Y('count:Q', axis=alt.Axis(title='Count')),
    tooltip=['DestinationZip', 'count']
).configure_axisX(
    labels=False
).properties(
    width=2500,
    height=500,
    title='Distribution of Destination Zip Codes'
).configure_title(
    anchor='middle'
)

alt.Chart(...)

In [152]:
# group by orign an destination zip and take sum of total packages
grouped_q1_df = q1_df.groupby(by=['OriginZip', 'DestinationZip']).sum().reset_index()

In [153]:
grouped_q1_df

OriginZip DestinationZip  OrderCount  Length  Width  Height   
0          02072          01003           2    29.0   19.0     5.0  \
1          02072          01005           3    10.0    8.0     3.0   
2          02072          01008           3    31.0   16.0     6.0   
3          02072          01010           3    46.0   26.0     7.0   
4          02072          01012           1    10.0    6.0     1.0   
...          ...            ...         ...     ...    ...     ...   
323933     98253          99783           6    43.0   56.0     6.0   
323934     98253          99803           1    11.0   14.0     1.0   
323935     98253          99824           2    27.0   34.0     2.0   
323936     98253          99825           3    26.0   35.0     4.0   
323937     98253          99830           3    39.0   49.0     3.0   

        WeightOunces  
0               42.0  
1               30.0  
2               17.0  
3               87.0  
4                7.0  
...              ...  
323933          60.0  
323934          20.0  
323935          63.0  
323936          68.0  
323937          82.0  

[323938 rows x 7 columns]

In [154]:
grouped_q1_df['Route'] = 'Origin: ' + grouped_q1_df['OriginZip'] + '- Destination: ' + grouped_q1_df['DestinationZip']

In [155]:
# since this is for September, 2022, just create a variable for # of days. This could be dynamic if we had more months, or likely would already have a feature denoting the month.
days_in_september = 30

In [156]:
grouped_q1_df['AveragePerDay'] = (grouped_q1_df['OrderCount'] / days_in_september).round().astype(int)

In [157]:
grouped_q1_df.sort_values('AveragePerDay',ascending=False)

OriginZip DestinationZip  OrderCount  Length   Width  Height   
186778     36039          71322         430   319.0   244.0   125.0  \
63923      17072          27529         270  2956.0  2194.0   831.0   
60769      17072          06359         239  2550.0  1913.0   648.0   
61639      17072          12964         215  2162.0  1691.0   648.0   
64317      17072          29372         205  2193.0  1666.0   505.0   
...          ...            ...         ...     ...     ...     ...   
115095     28159          47346           2    27.0    20.0     2.0   
115094     28159          47345           4    30.0    23.0    10.0   
115093     28159          47342           5    60.0    36.0    12.0   
115092     28159          47341           2    20.0    12.0     2.0   
323937     98253          99830           3    39.0    49.0     3.0   

        WeightOunces                              Route  AveragePerDay  
186778        1355.0  Origin: 36039- Destination: 71322             14  
63923         8469.0  Origin: 17072- Destination: 27529              9  
60769         8331.0  Origin: 17072- Destination: 06359              8  
61639         7265.0  Origin: 17072- Destination: 12964              7  
64317         5462.0  Origin: 17072- Destination: 29372              7  
...              ...                                ...            ...  
115095          30.0  Origin: 28159- Destination: 47346              0  
115094          71.0  Origin: 28159- Destination: 47345              0  
115093          79.0  Origin: 28159- Destination: 47342              0  
115092           9.0  Origin: 28159- Destination: 47341              0  
323937          82.0  Origin: 98253- Destination: 99830              0  

[323938 rows x 9 columns]

In [158]:
top_10000 = grouped_q1_df.sort_values('OrderCount', ascending=False)[:10000]

In [159]:
alt.Chart(top_10000).mark_bar().encode(
    x=alt.X('Route:N', axis=alt.Axis(title='Route'), sort=None),
    y=alt.Y('OrderCount:Q', axis=alt.Axis(title='Order Count')),
    tooltip=['Route:N', 'OrderCount']
).configure_axisX(
    labels=False
).properties(
    width=2500,
    height=500,
    title='Distribution of Zip Code Routes by Order Count - Top 10,000'
).configure_title(
    anchor='middle'
)

alt.Chart(...)

In [160]:
top_10000_avg = grouped_q1_df.sort_values('AveragePerDay', ascending=False)[:10000]

In [161]:
alt.Chart(top_10000_avg).mark_bar().encode(
    x=alt.X('Route:N', axis=alt.Axis(title='Route'), sort=None),
    y=alt.Y('AveragePerDay:Q', axis=alt.Axis(title='Average Per Day Count', tickMinStep=1)),
    tooltip=['Route', 'AveragePerDay', 'OrderCount']
).configure_axisX(
    labels=False
).properties(
    width=2500,
    height=500,
    title='Distribution of Average Packages per Day - Top 10,000'
).configure_title(
    anchor='middle'
)

alt.Chart(...)

In [162]:
# depends what we're trying to accomplish here

In [163]:
destination_monthly_total = grouped_q1_df.groupby('DestinationZip')['OrderCount'].sum().reset_index()

In [164]:
destination_monthly_total.sort_values('OrderCount', ascending=False)

DestinationZip  OrderCount
5893           27529        1266
16157          70645         987
7374           32702         926
4500           21015         895
7937           34770         871
...              ...         ...
11626          50361           1
7850           34249           1
2224           12188           1
567            03905           1
10904          48101           1

[22380 rows x 2 columns]

In [165]:
# https://www2.census.gov/geo/docs/maps-data/data/gazetteer/2020_Gazetteer/2020_Gaz_zcta_national.zip

In [166]:
zip_code_df = pd.read_csv('data/2020_Gaz_zcta_national.txt', sep='\t')

In [167]:
zip_code_df

GEOID       ALAND     AWATER  ALAND_SQMI  AWATER_SQMI   INTPTLAT   
0        601   166659744     799292      64.348        0.309  18.180555  \
1        602    79307538    4428428      30.621        1.710  18.361945   
2        603    81887203     181412      31.617        0.070  18.455183   
3        606   109579950      12487      42.309        0.005  18.158327   
4        610    93013430    4172059      35.913        1.611  18.294032   
...      ...         ...        ...         ...          ...        ...   
33139  99923    42495197       2117      16.407        0.001  56.000518   
33140  99925   144071036   34333408      55.626       13.256  55.550203   
33141  99926   343944586  292859017     132.798      113.074  55.138352   
33142  99927   589650055   18041593     227.665        6.966  56.239062   
33143  99929  5635963115  637274788    2176.058      246.053  56.370538   

       INTPTLONG                                                                                                                                    
0                                             -66.749961                                                                                            
1                                             -67.175597                                                                                            
2                                             -67.119887                                                                                            
3                                             -66.932928                                                                                            
4                                             -67.127156                                                                                            
...                                                  ...                                                                                            
33139                                        -130.037474                                                                                            
33140                                        -132.945947                                                                                            
33141                                        -131.470425                                                                                            
33142                                        -133.457924                                                                                            
33143                                        -131.693453                                                                                            

[33144 rows x 7 columns]

In [168]:
zip_code_df['DestinationZip'] = zip_code_df['GEOID'].astype(str).apply(fill_leading_zeros)

In [169]:
zip_code_df.head()

GEOID      ALAND   AWATER  ALAND_SQMI  AWATER_SQMI   INTPTLAT   
0    601  166659744   799292      64.348        0.309  18.180555  \
1    602   79307538  4428428      30.621        1.710  18.361945   
2    603   81887203   181412      31.617        0.070  18.455183   
3    606  109579950    12487      42.309        0.005  18.158327   
4    610   93013430  4172059      35.913        1.611  18.294032   

   INTPTLONG                                                                                                                                     
0                                         -66.749961                                                                                            \
1                                         -67.175597                                                                                             
2                                         -67.119887                                                                                             
3                                         -66.932928                                                                                             
4                                         -67.127156                                                                                             

  DestinationZip  
0          00601  
1          00602  
2          00603  
3          00606  
4          00610

In [170]:
merged_df = pd.merge(destination_monthly_total, zip_code_df, on='DestinationZip', how='left')

In [171]:
merged_df.columns

Index(['DestinationZip', 'OrderCount', 'GEOID', 'ALAND', 'AWATER',
       'ALAND_SQMI', 'AWATER_SQMI', 'INTPTLAT',
       'INTPTLONG                                                                                                                                  '],
      dtype='object')

In [172]:
merged_df = merged_df.rename(columns=lambda x: x.replace(' ', ''))

In [173]:
merged_df.columns

Index(['DestinationZip', 'OrderCount', 'GEOID', 'ALAND', 'AWATER',
       'ALAND_SQMI', 'AWATER_SQMI', 'INTPTLAT', 'INTPTLONG'],
      dtype='object')

In [174]:
merged_df = merged_df.dropna()

In [175]:
merged_df.head()

DestinationZip  OrderCount   GEOID        ALAND     AWATER  ALAND_SQMI   
2          01001          14  1001.0   29797658.0  2121390.0      11.505  \
3          01003          17  1003.0    1842387.0    12788.0       0.711   
4          01005          25  1005.0  114638390.0   666424.0      44.262   
5          01008          46  1008.0  139349132.0  5109088.0      53.803   
6          01010         214  1010.0   90055966.0  1421379.0      34.771   

   AWATER_SQMI   INTPTLAT  INTPTLONG  
2        0.819  42.062368 -72.625754  
3        0.005  42.389698 -72.524009  
4        0.257  42.418884 -72.112077  
5        1.973  42.190191 -72.954263  
6        0.549  42.128176 -72.205352

In [176]:
coords = merged_df[['INTPTLAT', 'INTPTLONG']].values

In [177]:
coords

array([[  42.062368,  -72.625754],
       [  42.389698,  -72.524009],
       [  42.418884,  -72.112077],
       ...,
       [  55.138352, -131.470425],
       [  56.239062, -133.457924],
       [  56.370538, -131.693453]])

In [178]:
dbscan_model = DBSCAN(eps=.5, min_samples=100)

In [179]:
labels = dbscan_model.fit_predict(coords)

In [180]:
merged_df['Cluster'] = labels

In [181]:
merged_df.head()

DestinationZip  OrderCount   GEOID        ALAND     AWATER  ALAND_SQMI   
2          01001          14  1001.0   29797658.0  2121390.0      11.505  \
3          01003          17  1003.0    1842387.0    12788.0       0.711   
4          01005          25  1005.0  114638390.0   666424.0      44.262   
5          01008          46  1008.0  139349132.0  5109088.0      53.803   
6          01010         214  1010.0   90055966.0  1421379.0      34.771   

   AWATER_SQMI   INTPTLAT  INTPTLONG  Cluster  
2        0.819  42.062368 -72.625754       -1  
3        0.005  42.389698 -72.524009       -1  
4        0.257  42.418884 -72.112077        0  
5        1.973  42.190191 -72.954263       -1  
6        0.549  42.128176 -72.205352        0

In [182]:
merged_df.groupby('Cluster').sum().sort_values('OrderCount', ascending=False)

DestinationZip  OrderCount   
Cluster                                                                  
-1       0100101003010080101201020010260102701030010320...     1252643  \
 1       0646806473064770651006512065130651406515065170...       77969   
 2       1500115003150041500515006150071500915012150141...       27721   
 0       0100501010010740108101094014200143801440014520...       26531   
 3       1725017311173201732117322173251732917340173441...       23817   
 7       9000390008900129001490015900169001790018900199...       17721   
 4       4630346304463074631046319463204632146322463234...       16154   
 5       4800248003480054800948015480174802248025480264...       14105   
 6       7500275009750107501375019750227502475025750287...       13032   
 8       9400294005940109401494015940209402294025940289...        9747   

               GEOID         ALAND        AWATER   ALAND_SQMI  AWATER_SQMI   
Cluster                                                                      
-1       797182080.0  3.961544e+12  8.514910e+10  1529560.629    32876.252  \
 1        11337365.0  2.658833e+10  9.202383e+08    10265.821      355.298   
 2         5714783.0  1.422644e+10  1.581470e+08     5492.845       61.059   
 0          855306.0  1.212901e+10  7.005828e+08     4683.034      270.500   
 3         6161093.0  1.151738e+10  5.622104e+08     4446.888      217.074   
 7        20198837.0  8.090379e+09  7.178983e+08     3123.714      277.180   
 4        12087993.0  8.882688e+09  2.281161e+08     3429.627       88.080   
 5         7137745.0  7.277033e+09  2.348130e+08     2809.680       90.662   
 6         9737210.0  7.601701e+09  3.250174e+08     2935.043      125.493   
 8        12487324.0  4.989675e+09  1.464088e+08     1926.521       56.531   

              INTPTLAT     INTPTLONG  
Cluster                               
-1       585135.843442 -1.392493e+06  
 1        37961.965796 -6.958073e+04  
 2        12393.746670 -2.453651e+04  
 0        13347.707926 -2.255541e+04  
 3        11473.051129 -2.263614e+04  
 7         7517.578994 -2.610674e+04  
 4         8617.459856 -1.810718e+04  
 5         6299.684242 -1.232279e+04  
 6         4238.259562 -1.250196e+04  
 8         4966.940926 -1.612285e+04

In [190]:
alt.Chart(merged_df).mark_point(size=60).encode(
    x=alt.X('INTPTLONG', axis=alt.Axis(title='Longitude')),
    y=alt.Y('INTPTLAT', axis=alt.Axis(title='Latitude')),
    color=alt.Color('Cluster:N'),
    tooltip=['DestinationZip', 'OrderCount', 'Cluster']
).properties(
    height=800,
    width=1600,
    title='Potential Sortation Facilities via DBSCAN - eps=0.5, min_samples=100'
).configure_legend(
    padding=10,
    cornerRadius=10,
    orient='top-right'
).interactive()

alt.Chart(...)